# TF CNN Classifier

To run this notebook on an another benchmark, use

```
papermill tf_cnn_classifier.ipynb tf_cnn_experiments/[DATASET NAME].ipynb -p DATASET [DATASET NAME]
```

In [1]:
DATASET = 'human_nontata_promoters'
VERSION = 0
BATCH_SIZE = 64
EPOCHS = 10

In [2]:
# Parameters
DATASET = "human_enhancers_ensembl"


In [3]:
print(DATASET, VERSION, BATCH_SIZE, EPOCHS)

human_enhancers_ensembl 0 64 10


# Data download

In [4]:
from pathlib import Path
import tensorflow as tf
import numpy as np

from genomic_benchmarks.loc2seq import download_dataset
from genomic_benchmarks.data_check import is_downloaded, info
from genomic_benchmarks.models.tf import vectorize_layer
from genomic_benchmarks.models.tf import basic_cnn_model_v0 as model

if not is_downloaded('human_nontata_promoters'):
    download_dataset('human_nontata_promoters')

2021-10-23 00:20:01.468705: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2021-10-23 00:20:01.468720: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


/home/petr/projects/genomic_benchmarks/src/genomic_benchmarks/loc2seq/with_biopython.py:8: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


2021-10-23 00:20:04.219115: E tensorflow/stream_executor/cuda/cuda_driver.cc:271] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
2021-10-23 00:20:04.219160: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (michle): /proc/driver/nvidia/version does not exist
2021-10-23 00:20:04.220944: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [5]:
info(DATASET)

Dataset `human_enhancers_ensembl` has 2 classes: negative, positive.

The lenght of genomic intervals ranges from 2 to 573, with average 268.8641324705183 and median 269.0.

Totally 154842 sequences have been found, 123872 for training and 30970 for testing.


/home/petr/projects/genomic_benchmarks/src/genomic_benchmarks/loc2seq/with_biopython.py:96: UserWarning: No version specified. Using version 0.
  warnings.warn(f"No version specified. Using version {metadata['version']}.")


train   test
negative  61936  15485
positive  61936  15485

## TF Dataset object

In [6]:
SEQ_PATH = Path.home() / '.genomic_benchmarks' / DATASET
CLASSES = [x.stem for x in (SEQ_PATH/'train').iterdir() if x.is_dir()]

train_dset = tf.keras.preprocessing.text_dataset_from_directory(
    SEQ_PATH / 'train',
    batch_size=BATCH_SIZE,
    class_names=CLASSES)

Found 123872 files belonging to 2 classes.


## Text vectorization

In [7]:
vectorize_layer.adapt(train_dset.map(lambda x, y: x))
# vectorize_layer.set_vocabulary(vocabulary=np.asarray(['a', 'c', 't', 'g', 'n']))
vectorize_layer.get_vocabulary()

2021-10-23 00:20:06.689398: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:185] None of the MLIR Optimization Passes are enabled (registered 2)


['', '[UNK]', 't', 'a', 'g', 'c', 'n']

In [8]:
def vectorize_text(text, label):
  text = tf.expand_dims(text, -1)
  return vectorize_layer(text)-2, label

train_ds = train_dset.map(vectorize_text)

## Model training

In [9]:
model.compile(loss=tf.keras.losses.BinaryCrossentropy(from_logits=True),
              optimizer='adam',
              metrics=tf.metrics.BinaryAccuracy(threshold=0.0))

In [10]:
history = model.fit(
    train_ds,
    epochs=EPOCHS)

Epoch 1/10


   1/1936 [..............................] - ETA: 24:05 - loss: 0.7152 - binary_accuracy: 0.4844

   3/1936 [..............................] - ETA: 1:01 - loss: 0.6976 - binary_accuracy: 0.5521 

   5/1936 [..............................] - ETA: 59s - loss: 0.6817 - binary_accuracy: 0.5813 

   7/1936 [..............................] - ETA: 1:01 - loss: 0.6706 - binary_accuracy: 0.6049

...

1930/1936 [============================>.] - ETA: 0s - loss: 0.4119 - binary_accuracy: 0.8163

1932/1936 [============================>.] - ETA: 0s - loss: 0.4119 - binary_accuracy: 0.8163

1934/1936 [============================>.] - ETA: 0s - loss: 0.4120 - binary_accuracy: 0.8163

1936/1936 [==============================] - ETA: 0s - loss: 0.4120 - binary_accuracy: 0.8163

1936/1936 [==============================] - 83s 43ms/step - loss: 0.4120 - binary_accuracy: 0.8163


## Evaluation on the test set

In [11]:
test_dset = tf.keras.preprocessing.text_dataset_from_directory(
    SEQ_PATH / 'test',
    batch_size=BATCH_SIZE,
    class_names=CLASSES)

test_ds =  test_dset.map(vectorize_text)

Found 30970 files belonging to 2 classes.


In [12]:
model.evaluate(test_ds)

  1/484 [..............................] - ETA: 1:35 - loss: 0.3584 - binary_accuracy: 0.8125

  7/484 [..............................] - ETA: 4s - loss: 0.4387 - binary_accuracy: 0.8080  

 12/484 [..............................] - ETA: 4s - loss: 0.4270 - binary_accuracy: 0.8099

 18/484 [>.............................] - ETA: 4s - loss: 0.4193 - binary_accuracy: 0.8003

 22/484 [>.............................] - ETA: 4s - loss: 0.4220 - binary_accuracy: 0.8054

...

475/484 [============================>.] - ETA: 0s - loss: 0.4228 - binary_accuracy: 0.8118

479/484 [============================>.] - ETA: 0s - loss: 0.4232 - binary_accuracy: 0.8114

482/484 [============================>.] - ETA: 0s - loss: 0.4230 - binary_accuracy: 0.8116

484/484 [==============================] - 5s 11ms/step - loss: 0.4231 - binary_accuracy: 0.8115


[0.4231271743774414, 0.8114627003669739]